In [1]:
import vectorbt as vbt
import numpy as np
from itertools import combinations, product

In [2]:
# Fetch daily price of Bitcoin
price = vbt.utils.data.download("AAL", start='2020-1-1')['Close']
price = price.vbt.split_into_ranges(n=3)

In [3]:
fast_windows, slow_windows, signal_windows = vbt.indicators.create_param_combs(
    (product, (combinations, np.arange(2, 51, 1), 2), np.arange(2, 21, 1)))

# Run MACD indicator
macd_ind = vbt.MACD.run(
    price,
    fast_window=fast_windows,
    slow_window=slow_windows,
    signal_window=signal_windows,
    hide_params=['macd_ewm', 'signal_ewm']
)

# Long when MACD is above zero AND signal
entries = macd_ind.macd_above(0) & macd_ind.macd_above(macd_ind.signal)

# Short when MACD is below zero OR signal
exits = macd_ind.macd_below(0) | macd_ind.macd_below(macd_ind.signal)


In [4]:
portfolio = vbt.Portfolio.from_signals(
    price.vbt.tile(len(fast_windows)), entries, exits, fees=0.001, freq='1D')

In [9]:
# Draw all window combinations as a 3D volume
fig = portfolio.total_return().vbt.volume(
    x_level='macd_fast_window',
    y_level='macd_slow_window',
    z_level='macd_signal_window',
    slider_level='range_start',
    trace_kwargs=dict(
        colorbar=dict(
            title='Total return', 
            tickformat='%'
        )
    )
)
fig.show()